# Housing rental & venues in Gainesville, FL - Data

### Import libraries

In [3]:
# Import libraries
import pandas as pd
from geopy.distance import geodesic
import requests
from sklearn.cluster import KMeans
import folium
import geopandas


# Pandas output
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', None)

### Create a function to get apartments for rent in Gainesville

In [8]:
# Get apartment for rent in Gainesville
def get_apartment_for_rent(limit=100):

    # Apartments list
    apartments_list = []

    # API request URL
    url = "https://realtor.p.rapidapi.com/properties/v2/list-for-rent"

    querystring = {"city": "Gainesville",
                   "state_code": "FL",
                   "limit": limit,
                   "offset": "0",
                   "sort": "relevance"}

    headers = {
        'x-rapidapi-key': " ",
        'x-rapidapi-host': "realtor.p.rapidapi.com"
    }

    # Make the GET request
    response = requests.request("GET", url, headers=headers, params=querystring).json()['properties']

    # Return only relevant information for each nearby apartment
    apartments_list.append([(
        apt['address']['line'],
        apt['address']['postal_code'],
        apt['address']['lat'],
        apt['address']['lon'],
        apt['community']['price_min'],
        apt['community']['price_max'],
        apt['community']['sqft_min'],
        apt['community']['sqft_max']) for apt in response])

    # Apartment dataframe
    apartments_for_rent = pd.DataFrame([item for apartments_list in apartments_list for item in apartments_list])

    # Apartment columns
    apartments_for_rent.columns = ['Address', 'ZipCode', 'Latitude', 'Longitude', 'Min Price', 'Max Price', 'Min Sqft', 'Max Sqft']

    # Return apartment dataframe
    return apartments_for_rent

### Create a function to get the venues for every apartment in Gainesville

In [9]:
# Get the venues for every apartment in Gainesville
def get_nearby_venues(address, latitudes, longitudes, avg_prices, radius=804.672):

    # Define Foursquare Credentials and Version
    CLIENT_ID = ' '  # your Foursquare ID
    CLIENT_SECRET = ' '  # your Foursquare Secret
    VERSION = '20180605'  # Foursquare API version
    LIMIT = 100  # A default Foursquare API limit value

    # Venues list
    venues_list = []

    # Get the venues nearby for each apartment
    for addrss, lat, lng, avg_price in zip(address, latitudes, longitudes, avg_prices):

        # Create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID,
            CLIENT_SECRET,
            VERSION,
            lat,
            lng,
            radius,
            LIMIT)

        # Make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']

        # Return only relevant information for each nearby venue
        venues_list.append([(
            addrss,
            lat,
            lng,
            avg_price,
            v['venue']['name'],
            v['venue']['location']['lat'],
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']) for v in results])

    # Venues dataframe
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])

    # Venues columns
    nearby_venues.columns = ['Address',
                             'Latitude',
                             'Longitude',
                             'Avg Price',
                             'Venue',
                             'Venue Latitude',
                             'Venue Longitude',
                             'Venue Category']

    # Return venues
    return nearby_venues

### Create a function to get the distance between point A to point B

In [12]:
# Get distance between two points in miles
def get_distance_between_two_points(point_A, point_two_lat_lng, df):
    # Distance list
    distance_ = []

    # Get the distance for every point B in the dataframe
    for i in range(df.count()):
        # Point B (This is all the point that you want to measure from df)
        point_B = (point_two_lat_lng[0][i], point_two_lat_lng[1][i])

        # Distance in miles from one point to the other one
        distance_.append(geodesic(point_A, point_B).miles) # Add every distance to a list

    # Return distance
    return distance_

### Define the geopoints for the University of Florida

In [10]:
# University of Florida geopoints
uf_lat_lng = (29.6436, -82.3549)

uf_lat_lng

(29.6436, -82.3549)

### Apartments for rent in Gainesville
* Call the function to get the apartments
* Find the average price for each apartment by (adding avg min & avg max and then dividing the result by two) and then add the result to the apt dataframe 
* Define the Address, Latitude, Avg Price, and Apt latitude and longitude variable
* Get the distance between each apartment to the University (UF) and add it to the dataframe
* Print the apartments for rent

In [13]:
# Apartments for rent in Gainesville (Dataframe
apt_for_rent_df = get_apartment_for_rent()

# Find average rent price
apt_for_rent_df['Avg Price'] = (apt_for_rent_df['Min Price'] + apt_for_rent_df['Max Price']) / 2

# Find average rent sqft
apt_for_rent_df['Avg Sqft'] = (apt_for_rent_df['Min Sqft'] + apt_for_rent_df['Max Sqft']) / 2


# Drop columns that we are not going to use
apt_for_rent_df.drop(columns={'Min Price', 'Max Price', 'Min Sqft', 'Max Sqft'}, inplace=True)


# Variables
apt_address = apt_for_rent_df['Address']
apt_lat_df = apt_for_rent_df['Latitude']
apt_lng_df = apt_for_rent_df['Longitude']
apt_avg_price = apt_for_rent_df['Avg Price']


# Apartments latitude and longitude
apartments_lat_lng = (apt_lat_df, apt_lng_df)


# Get the distance between the apartment and the University of Florida
apt_for_rent_df['UF-Apt Distance'] = get_distance_between_two_points(uf_lat_lng, apartments_lat_lng, apt_address)
apt_distance = apt_for_rent_df['UF-Apt Distance']

# Print result
apt_for_rent_df.head()

Address ZipCode   Latitude  Longitude  Avg Price  Avg Sqft  \
0    311 SW 13th St   32601  29.649057 -82.338943      854.0     935.5   
1  6001 SW 75th Ter   32608  29.599560 -82.422520     1513.5    1119.5   
2  3980 SW 24th Ave   32607  29.630842 -82.383229     1812.0    1056.5   
3   3000 SW 35th Pl   32608  29.623600 -82.367160      709.0    1356.5   
4  1101 NW 39th Ave   32609  29.688300 -82.336860     1085.0     922.5   

   UF-Apt Distance  
0         1.031009  
1         5.075511  
2         1.917743  
3         1.562635  
4         3.264448

### Apt for rent shape
* In the dataframe are 100 apartments and 7 column with differents points

In [14]:
apt_for_rent_df.shape

(100, 7)

### Create a map of the apartments for rent in Gainesville using latitude and longitude values

In [8]:
# Map of apartments for rent in Gainesville using latitude and longitude values
def create_apt_for_rent_map(lat_df, lng_df):
    # Create map of Toronto, Ontario using latitude and longitude values
    apt_for_rent_map = folium.Map(location=[lat_df, lng_df], zoom_start=11)

    # Add markers to map
    for lat, lng, address, avg_prices in zip(apt_for_rent_df['Latitude'], apt_for_rent_df['Longitude'], 
                                apt_for_rent_df['Address'], apt_for_rent_df['Avg Price']):
        
        # Label the map
        label = '{}, ${}'.format(address, avg_prices)
        label = folium.Popup(label, parse_html=True)
        
        # Make circle in the map for each neighborhood
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(apt_for_rent_map)
    
    # Return map
    return apt_for_rent_map


### Apartments for rent in Gainesville Map
* Create the apartments for rent in Gainesville map
* Show the map

In [9]:
# Map
apt_for_rent_map = create_apt_for_rent_map(29.6436, -82.3549)

# Display Map
apt_for_rent_map

### Apartments for rent and venues in Gainesville
* Call the function to get the venues with the apartments for rent
* Define the Venue, Venue Latitude, Venue Longitude, and Venue Category variables
* Print the venues with the apartments for rent 

In [10]:
# Gainesville dataframe with venues and apartments for rent
venues_nearby_df = get_nearby_venues(apt_address, apt_lat_df, apt_lng_df, apt_avg_price)


# Variables
v_name = venues_nearby_df['Venue']
v_lat_df = venues_nearby_df['Venue Latitude']
v_lng_df = venues_nearby_df['Venue Longitude']
v_category = venues_nearby_df['Venue Category']

# Print result
venues_nearby_df.head()

Address   Latitude  Longitude  Avg Price                Venue  \
0  311 SW 13th St  29.649057 -82.338943      854.0     Leonardo's Pizza   
1  311 SW 13th St  29.649057 -82.338943      854.0          Karma Cream   
2  311 SW 13th St  29.649057 -82.338943      854.0  Chick-fil-A Express   
3  311 SW 13th St  29.649057 -82.338943      854.0               Publix   
4  311 SW 13th St  29.649057 -82.338943      854.0          Chick-fil-A   

   Venue Latitude  Venue Longitude        Venue Category  
0       29.651971       -82.338585           Pizza Place  
1       29.651906       -82.335961        Ice Cream Shop  
2       29.647178       -82.341564  Fast Food Restaurant  
3       29.653261       -82.338995         Grocery Store  
4       29.652259       -82.339679          Food Service

### Venues with apartments shape

* In the dataframe are 2843 venues and 8 column with differents points

In [11]:
venues_nearby_df.shape

(2843, 8)

### Create a map of the venues with apartments for rent in Gainesville using latitude and longitude values

In [12]:
# Map of Toronto, Ontario using latitude and longitude values
def create_venues_nearby_map(lat_df, lng_df):
    # Create map of Toronto, Ontario using latitude and longitude values
    venues_nearby_map = folium.Map(location=[lat_df, lng_df], zoom_start=11)

    # Add markers to map
    for lat, lng, venues, venues_category in zip(venues_nearby_df['Venue Latitude'], venues_nearby_df['Venue Longitude'], 
                                venues_nearby_df['Venue'], venues_nearby_df['Venue Category']):
        
        # Label the map
        label = '{}, {}'.format(venues, venues_category)
        label = folium.Popup(label, parse_html=True)
        
        # Make circle in the map for each neighborhood
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='blue',
            fill_opacity=0.7,
            parse_html=False).add_to(venues_nearby_map)
    
    # Return map
    return venues_nearby_map


### Venues with apartments for rent in Gainesville Map

* Create the venues with apartments for rent in Gainesville map
* Show the map

In [13]:
# Map
venues_nearby_map = create_venues_nearby_map(29.6436, -82.3549)

# Display Map
venues_nearby_map

### Create choropleth map for Gainesville
* Read json file to get the geopoints of gainesville
* Define Gainesville latitude and longitude variables
* Create Gainesville map
* Create Gainesville choropleth map
* Show Gainesville choropleth map

In [25]:
# Read json file
filename = "gainesville_geo.json"
gainesville_geo = geopandas.read_file(filename)
gainesville_geo.head()


# Gainesville latitude and longitude
latitude = 29.6516
longitude = -82.3248


# Create Gainesville map
gainesville_map = folium.Map(location=[latitude, longitude], zoom_start=10)


# Create choropleth map
gainesville_map.choropleth(
    geo_data=gainesville_geo,
    fill_color='blue',
    highlight=True
)

# Display map
gainesville_map